In [2]:
import wrds
import pandas as pd
import numpy as np


db = wrds.Connection()

Enter your WRDS username [shuhao]:nosleep3
Enter your password:········
WRDS recommends setting up a .pgpass file.
You can find more info here:
https://www.postgresql.org/docs/9.5/static/libpq-pgpass.html.
Loading library list...
Done


###  1. Input data

In [55]:
# IBES Recommendation data and link with CRSP
df_ibes_rec = pd.read_csv('/Users/shuhao/Dropbox/Textual Analysis Project/Data/IBES/IBES_Recommendation.csv')
df_ibes_crsp_link = pd.read_csv('/Users/shuhao/Dropbox/Textual Analysis Project/Data/IBES/CRSP_IBES_link_table.csv')

# Compustat Short Interest data and link with CRSP
df_comp_shrt_int = pd.read_csv('/Users/shuhao/Dropbox/Textual Analysis Project/Data/Compustat/compustat_short_interest.csv')
df_comp_crsp_link = pd.read_csv('/Users/shuhao/Dropbox/Textual Analysis Project/Data/Compustat/Compustat_CRSP_link_table.csv')

# read CRSP datafile
df_crsp = pd.read_csv('/Users/shuhao/Dropbox/Textual Analysis Project/Data/CRSP/CRSP_1992_01_01_2018_06_30.csv')

In [4]:
print(df_comp_crsp_link.head(5))
print(df_comp_shrt_int.head(5))
print(df_ibes_crsp_link.head(5))
print(df_ibes_rec.head(5))
print(df_crsp.head())

   gvkey  lpermno
0   1000    25881
1   1001    10015
2   1002    10023
3   1003    10031
4   1004    54594
   Unnamed: 0  level_0        date  index  gvkey  iid  shortint    datadate  \
0           0        0  1977-07-15      0   1000    1    1000.0  07/15/1977   
1           1        1  1977-11-15      1   1000    1    2000.0  11/15/1977   
2           2        2  1977-09-15      2   1000    1    2400.0  09/15/1977   
3           3        3  1977-08-15      3   1000    1    1000.0  08/15/1977   
4           4        4  1978-06-15      4   1000    1     300.0  06/15/1978   

   tic cusip  
0  NaN   NaN  
1  NaN   NaN  
2  NaN   NaN  
3  NaN   NaN  
4  NaN   NaN  
   Unnamed: 0 ticker  permno                             cname  \
0           0   0000   14471                TALMER BANCORP INC   
1           1   0001   14392                    EP ENERGY CORP   
2           2   0004   14418  AMERICAN CAPITAL SENIOR FLTG LTD   
3           3   000R   14378                       CARECOM INC 

### 2. Intersect sets to get the matched PERMNO

In [5]:
def intersect(a, b):
    return list(set(a) & set(b))

print(len(set(df_comp_crsp_link['lpermno'])))
print(len(set(df_ibes_crsp_link['permno'])))

merge_permno = intersect(df_comp_crsp_link['lpermno'], df_ibes_crsp_link['permno'])
print(len(merge_permno))
print(merge_permno[:10])

27455
18082
17076
[16384, 82576, 65541, 65542, 87383, 81922, 10925, 89952, 76462, 32791]


### 3. Adjust both the links according to the matched PERMNO

In [6]:
permno = pd.DataFrame(merge_permno, columns=['permno'])

# Save short interest according to the permno 
comp_crsp_link = permno.merge(df_comp_crsp_link, how='left', left_on='permno', right_on='lpermno')

print(len(comp_crsp_link))
comp_crsp_link.head()

17416


permno   gvkey  lpermno
0   16384   23093    16384
1   82576   61508    82576
2   65541    3504    65541
3   65542    8931    65542
4   87383  126137    87383

In [7]:
# Save IBES recommendation according to the permno
ibes_crsp_link = df_ibes_crsp_link.merge(permno, how='right', on='permno')

print(len(ibes_crsp_link))
print(ibes_crsp_link.head(5))

17205
   Unnamed: 0 ticker  permno                             cname  \
0           0   0000   14471                TALMER BANCORP INC   
1           1   0001   14392                    EP ENERGY CORP   
2           2   0004   14418  AMERICAN CAPITAL SENIOR FLTG LTD   
3           3   000R   14378                       CARECOM INC   
4           4   000V   14423      EIGER BIOPHARMACEUTICALS INC   

                            comnam  name_similarity  score  
0               TALMER BANCORP INC              100      0  
1                  E P ENERGY CORP               97      0  
2  AMERICAN CAPITAL SR FLOATING LT               86      0  
3                     CARE COM INC               96      0  
4     EIGER BIOPHARMACEUTICALS INC              100      0  


### 4. Data Analysis

In [56]:
# sort ibes dataset by ticker and dates
df_ibes_rec.sort_values(by=['ticker', 'anndats', 'anntims'], inplace=True)
df_ibes_rec.head(5)


Unnamed: 0 ticker     cusip oftic           cname     anndats  anntims  \
2           2   0000  87482X10  TLMR  TALMER BANCORP  2014-03-09  61500.0   
0           0   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   1200.0   
1           1   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   1500.0   
3           3   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10  24480.0   
4           4   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10  27900.0   

   ireccd  
2       2  
0       2  
1       2  
3       1  
4       3

In [183]:
# get the mean of recommendation groupby ticker and date as indicator of sentiment
# "1" means positive (strong buy 1; buy 2). "0" means negative (hold 3; underperform 4; strong sell 5) 

sentiment = df_ibes_rec.groupby(['ticker', 'anndats'])['ireccd'].mean()

sentiment = pd.DataFrame(sentiment)
sentiment.loc[sentiment['ireccd'] < 3, 'sentiment'] = 1
sentiment.loc[sentiment['ireccd'] >= 3, 'sentiment'] = 0

sentiment[:5]

ireccd  sentiment
ticker anndats                      
0000   2014-03-09     2.0        1.0
       2014-03-10     2.0        1.0
       2014-12-03     1.0        1.0
       2015-04-30     3.0        0.0
       2015-07-30     3.0        0.0

In [184]:
sentiment.reset_index(inplace=True)

# merge the ibes recommendation sentiment data with the crsp_ibes link
sentiment = sentiment.merge(ibes_crsp_link, how='right', left_on='ticker', right_on='ticker')
sentiment = sentiment[['ticker', 'anndats', 'ireccd', 'sentiment', 'permno', 'cname']]
sentiment.head()
    

ticker     anndats  ireccd  sentiment  permno               cname
0   0000  2014-03-09     2.0        1.0   14471  TALMER BANCORP INC
1   0000  2014-03-10     2.0        1.0   14471  TALMER BANCORP INC
2   0000  2014-12-03     1.0        1.0   14471  TALMER BANCORP INC
3   0000  2015-04-30     3.0        0.0   14471  TALMER BANCORP INC
4   0000  2015-07-30     3.0        0.0   14471  TALMER BANCORP INC

In [12]:
# # sort values of ibes and crsp to prepare for the loop
# sentiment.sort_values(by=['permno', 'anndats'], inplace=True)
df_crsp.sort_values(by=['PERMNO', 'date'], inplace=True)
df_crsp.head()

PERMNO        date SICCD     PRC        RET  SHROUT    sprtrn
0      10001  01/02/1992  4920  14.500   0.000000  1075.0  0.000408
1011   10001  01/02/1996  4920  -9.125  -0.026667  2281.0  0.007793
1265   10001  01/02/1997  4920   8.125   0.000000  2357.0 -0.005036
1518   10001  01/02/1998  4920   9.000   0.000000  2395.0  0.004750
2274   10001  01/02/2001  4920   9.875   0.012821  2498.0 -0.028032

In [327]:
df_crsp['ret_shift_1'] = df_crsp.groupby(['permno'])['RET'].shift(1)
df_crsp['ret_shift_2'] = df_crsp.groupby(['permno'])['RET'].shift(2)
df_crsp['ret_shift_3'] = df_crsp.groupby(['permno'])['RET'].shift(3)
df_crsp['ret_1'] = df_crsp.groupby(['permno'])['RET'].shift(-1)
df_crsp['ret_2'] = df_crsp.groupby(['permno'])['RET'].shift(-2)
df_crsp['ret_3'] = df_crsp.groupby(['permno'])['RET'].shift(-3)


df_crsp.head(10)



permno       date SICCD     PRC        RET  SHROUT    sprtrn ret_shift_1  \
0   10001 1992-01-02  4920  14.500   0.000000  1075.0  0.000408         NaN   
1   10001 1992-01-03  4920  14.500   0.000000  1075.0  0.004985    0.000000   
2   10001 1992-01-06  4920  14.500   0.000000  1075.0 -0.003291    0.000000   
3   10001 1992-01-07  4920  14.500   0.000000  1075.0 -0.001340    0.000000   
4   10001 1992-01-08  4920  15.125   0.043103  1075.0  0.001677    0.000000   
5   10001 1992-01-09  4920  14.500  -0.041322  1075.0 -0.001172    0.043103   
6   10001 1992-01-10  4920  14.500   0.000000  1075.0 -0.006010   -0.041322   
7   10001 1992-01-13  4920  14.500   0.000000  1075.0 -0.001831    0.000000   
8   10001 1992-01-14  4920  14.500   0.000000  1075.0  0.014722    0.000000   
9   10001 1992-01-15  4920  15.000   0.034483  1075.0  0.000785    0.000000   

  ret_shift_2 ret_shift_3      ret_1      ret_2      ret_3  
0         NaN         NaN   0.000000   0.000000   0.000000  
1         NaN         NaN   0.000000   0.000000   0.043103  
2    0.000000         NaN   0.000000   0.043103  -0.041322  
3    0.000000    0.000000   0.043103  -0.041322   0.000000  
4    0.000000    0.000000  -0.041322   0.000000   0.000000  
5    0.000000    0.000000   0.000000   0.000000   0.000000  
6    0.043103    0.000000   0.000000   0.000000   0.034483  
7   -0.041322    0.043103   0.000000   0.034483  -0.050000  
8    0.000000   -0.041322   0.034483  -0.050000   0.052632  
9    0.000000    0.000000  -0.050000   0.052632  -0.016667

In [330]:
df_crsp[df_crsp['permno'] == 10220]

permno       date SICCD    PRC        RET    SHROUT    sprtrn  \
277182   10220 2010-08-02  3569  23.15          C  116226.0  0.022023   
277183   10220 2010-08-03  3569  22.37  -0.033693  116226.0 -0.004796   
277184   10220 2010-08-04  3569  23.51   0.050961  116226.0  0.006051   
277185   10220 2010-08-05  3569  24.68   0.049766  116226.0 -0.001269   
277186   10220 2010-08-06  3569  24.11  -0.023096  116226.0 -0.003704   
277187   10220 2010-08-09  3569  23.76  -0.014517  116226.0  0.005483   
277188   10220 2010-08-10  3569  23.46  -0.012626  116226.0 -0.005967   
277189   10220 2010-08-11  3569  22.95  -0.021739  116226.0 -0.028179   
277190   10220 2010-08-12  3569  22.39  -0.024401  116226.0 -0.005379   
277191   10220 2010-08-13  3569  22.03  -0.016079  116226.0 -0.004024   
277192   10220 2010-08-16  3569  22.14   0.004993  116226.0  0.000120   
277193   10220 2010-08-17  3569  22.61   0.021229  116226.0  0.012192   
277194   10220 2010-08-18  3569  23.04   0.019018  116226.0  0.001483   
277195   10220 2010-08-19  3569  23.51   0.020399  116226.0 -0.016935   
277196   10220 2010-08-20  3569  23.46  -0.002127  116226.0 -0.003663   
277197   10220 2010-08-23  3569  23.48   0.000853  116226.0 -0.004040   
277198   10220 2010-08-24  3569  23.15  -0.014055  116226.0 -0.014512   
277199   10220 2010-08-25  3569  23.01  -0.006047  116226.0  0.003289   
277200   10220 2010-08-26  3569  22.62  -0.016949  116226.0 -0.007685   
277201   10220 2010-08-27  3569  23.41   0.034925  116226.0  0.016587   
277202   10220 2010-08-30  3569  23.25  -0.006835  116226.0 -0.014719   
277203   10220 2010-08-31  3569  22.40  -0.036559  116226.0  0.000391   
277204   10220 2010-09-01  3569  22.82   0.018750  116226.0  0.029505   
277205   10220 2010-09-02  3569  22.70  -0.005258  116226.0  0.009081   
277206   10220 2010-09-03  3569  22.48  -0.009692  116226.0  0.013219   
277207   10220 2010-09-07  3569  22.30  -0.008007  116226.0 -0.011471   
277208   10220 2010-09-08  3569  22.04  -0.011659  116226.0  0.006439   
277209   10220 2010-09-09  3569  22.24   0.009074  116226.0  0.004832   
277210   10220 2010-09-10  3569  22.00  -0.010791  116226.0  0.004863   
277211   10220 2010-09-13  3569  22.02   0.000909  116226.0  0.011131   
...        ...        ...   ...    ...        ...       ...       ...   
279145   10220 2018-05-18  3443  68.44   0.001024   99636.0 -0.002632   
279146   10220 2018-05-21  3443  68.59   0.002192   99636.0  0.007387   
279147   10220 2018-05-22  3443  67.99  -0.008748   99636.0 -0.003136   
279148   10220 2018-05-23  3443  68.04   0.000735   99636.0  0.003248   
279149   10220 2018-05-24  3443  68.10   0.000882   99636.0 -0.002023   
279150   10220 2018-05-25  3443  67.78  -0.004699   99636.0 -0.002357   
279151   10220 2018-05-29  3443  67.25  -0.007819   99636.0 -0.011564   
279152   10220 2018-05-30  3443  67.49   0.003569   99636.0  0.012696   
279153   10220 2018-05-31  3443  66.74  -0.011113   99680.0 -0.006880   
279154   10220 2018-06-01  3443  67.45   0.010638   99680.0  0.010849   
279155   10220 2018-06-04  3443  66.90  -0.008154   99680.0  0.004480   
279156   10220 2018-06-05  3443  67.17   0.004036   99680.0  0.000703   
279157   10220 2018-06-06  3443  67.39   0.003275   99680.0  0.008567   
279158   10220 2018-06-07  3443  66.58  -0.012020   99680.0 -0.000714   
279159   10220 2018-06-08  3443  67.36   0.011715   99680.0  0.003126   
279160   10220 2018-06-11  3443  67.57   0.003118   99680.0  0.001069   
279161   10220 2018-06-12  3443  66.79  -0.011544   99680.0  0.001743   
279162   10220 2018-06-13  3443  66.47  -0.004791   99680.0 -0.004026   
279163   10220 2018-06-14  3443  65.91  -0.008425   99680.0  0.002472   
279164   10220 2018-06-15  3443  65.39  -0.007890   99680.0 -0.001017   
279165   10220 2018-06-18  3443  65.08  -0.004741   99680.0 -0.002126   
279166   10220 2018-06-19  3443  62.95  -0.032729   99680.0 -0.004023   
279167   10220 2018-06-20  3443  63.07   0.001906   99680.0  0.001

In [227]:
from datetime import timedelta
from datetime import datetime
import numpy as np

# if permno is nan, delete the whole row
sentiment.dropna(inplace=True)
sentiment.sort_values(by=['permno', 'anndats'], inplace=True)
print(sentiment.head())
df_crsp.sort_values(by=['PERMNO', 'date'], inplace=True)




KeyError: 'anndats'

In [236]:
sentiment['date'] = pd.to_datetime(sentiment['date'])
sentiment['permno'].apply(lambda x: str(x))
df_crsp['permno'].apply(lambda x: str(x))


0           10001
1           10001
2           10001
3           10001
4           10001
5           10001
6           10001
7           10001
8           10001
9           10001
10          10001
11          10001
12          10001
13          10001
14          10001
15          10001
16          10001
17          10001
18          10001
19          10001
20          10001
21          10001
22          10001
23          10001
24          10001
25          10001
26          10001
27          10001
28          10001
29          10001
            ...  
37385878    93436
37385879    93436
37385880    93436
37385881    93436
37385882    93436
37385883    93436
37385884    93436
37385885    93436
37385886    93436
37385887    93436
37385888    93436
37385889    93436
37385890    93436
37385891    93436
37385892    93436
37385893    93436
37385894    93436
37385895    93436
37385896    93436
37385897    93436
37385898    93436
37385899    93436
37385900    93436
37385901    93436
37385902  

In [331]:
# df_crsp.rename(columns={'PERMNO':'permno'}, inplace=True)
# sentiment.rename(columns={'anndats':'date'}, inplace=True)

merge_sentiment_crsp = pd.merge(sentiment, df_crsp, how='left', on=['permno', 'date'])
merge_sentiment_crsp.head()


ticker       date  ireccd  sentiment  permno            cname SICCD     PRC  \
0   GFGC 1993-11-04     3.0        0.0   10001  GAS NATURAL INC  4920  16.500   
1   GFGC 1994-02-08     1.0        1.0   10001  GAS NATURAL INC  4920  17.750   
2   GFGC 1994-12-07     3.0        0.0   10001  GAS NATURAL INC  4920   8.625   
3   GFGC 2011-01-06     1.0        1.0   10001  GAS NATURAL INC  4925  10.430   
4   GFGC 2014-01-31     3.0        0.0   10001  GAS NATURAL INC  4925   9.170   

         RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3     ret_1  \
0  -0.057143   1091.0 -0.011943    0.000000    0.000000    0.014493  0.030303   
1   0.021583   1091.0 -0.001484   -0.007143   -0.014085    0.014286  0.000000   
2   0.029851   2211.0 -0.004149    0.000000   -0.032000    0.044776  0.000000   
3   0.002885   7834.0 -0.002123   -0.003831   -0.000957   -0.006654  0.005753   
4  -0.037775  10452.0 -0.006465    0.003158    0.024811   -0.013830  0.000000   

       ret_2      ret_3  
0   0.029412  -0.057143  
1  -0.014085   0.000000  
2  -0.072464   0.000000  
3   0.000953   0.003810  
4   0.033806  -0.018987

In [333]:
merge_sentiment_crsp.isna().sum()


ticker             0
date               0
ireccd             0
sentiment          0
permno             0
cname              0
SICCD          31100
PRC            31788
RET            31231
SHROUT         31189
sprtrn         31100
ret_shift_1    31360
ret_shift_2    31528
ret_shift_3    31631
ret_1          31274
ret_2          31331
ret_3          31379
dtype: int64

In [336]:
missing_crsp_sent = merge_sentiment_crsp[(merge_sentiment_crsp['SICCD'].isnull()) &
                                        (merge_sentiment_crsp['PRC'].isnull()) &
                                        (merge_sentiment_crsp['RET'].isnull()) &
                                        (merge_sentiment_crsp['SHROUT'].isnull()) &
                                        (merge_sentiment_crsp['sprtrn'].isnull()) &
                                        (merge_sentiment_crsp['ret_shift_1'].isnull()) &
                                        (merge_sentiment_crsp['ret_shift_2'].isnull()) &
                                        (merge_sentiment_crsp['ret_shift_3'].isnull()) &
                                        (merge_sentiment_crsp['ret_1'].isnull()) &
                                        (merge_sentiment_crsp['ret_2'].isnull()) &
                                        (merge_sentiment_crsp['ret_3'].isnull()) ]
missing_index = missing_crsp_sent.index
missing_crsp_sent


ticker       date  ireccd  sentiment  permno  \
209      PLUS 2001-11-17    3.00        0.0   10032   
235      PLUS 2002-08-04    3.00        0.0   10032   
241      PLUS 2002-09-08    2.50        1.0   10032   
271      PLUS 2003-09-13    3.00        0.0   10032   
295      PLUS 2004-11-07    1.00        1.0   10032   
311      PLUS 2006-01-08    4.00        0.0   10032   
339      PLUS 2008-06-01    1.00        1.0   10032   
371      PLUS 2011-10-08    3.00        0.0   10032   
400      PLUS 2017-08-27    2.00        1.0   10032   
537      CCCO 1994-04-27    2.00        1.0   10048   
596       HGR 2002-08-04    3.00        0.0   10051   
599       HGR 2002-09-08    2.00        1.0   10051   
647       HGR 2016-02-15    3.00        0.0   10051   
648       HGR 2016-02-29    3.00        0.0   10051   
649       HGR 2018-01-22    1.00        1.0   10051   
693      TTOY 2003-01-24    1.00        1.0   10064   
694      TTOY 2003-03-28    1.00        1.0   10064   
695      TTOY 2003-08-05    1.00        1.0   10064   
962      SUNW 2002-03-17    4.00        0.0   10078   
976      SUNW 2002-08-04    4.00        0.0   10078   
981      SUNW 2002-09-08    3.25        0.0   10078   
993      SUNW 2003-01-12    3.00        0.0   10078   
1003     SUNW 2003-09-13    5.00        0.0   10078   
1006     SUNW 2003-10-05    4.00        0.0   10078   
1040     SUNW 2005-03-27    3.00        0.0   10078   
1045     SUNW 2005-06-05    5.00        0.0   10078   
1050     SUNW 2005-09-25    1.00        1.0   10078   
1061     SUNW 2006-05-29    2.00        1.0   10078   
1079     SUNW 2007-08-05    2.00        1.0   10078   
1093     SUNW 2008-06-01    4.00        0.0   10078   
...       ...        ...     ...        ...     ...   
678887   ACMH 2010-04-23    2.00        1.0   93391   
678904   NVWH 2008-01-04    2.00        1.0   93395   
678956   RLOC 2011-10-08    1.00        1.0   93400   
679010   BORN 2011-12-04    1.00        1.0   93406   
679019   ONEH 2011-07-10    2.00        1.0   93418   
679037   ONEH 2013-07-07    4.00        0.0   93418   
679079   HPPP 2016-08-27    1.00        1.0   93419   
679120   OASS 2011-08-14    2.00        1.0   93420   
679146   OASS 2012-06-17    2.00        1.0   93420   
679268   OASS 2017-05-29    4.00        0.0   93420   
679286    QEP 2010-06-22    1.00        1.0   93422   
679287    QEP 2010-06-28    3.00        0.0   93422   
679335    QEP 2013-04-06    2.00        1.0   93422   
679386    QEP 2017-05-29    3.00        0.0   93422   
679487   CBOH 2010-07-25    3.00        0.0   93429   
679495   CBOH 2010-12-18    3.00        0.0   93429   
679510   CBOH 2011-10-08    3.00        0.0   93429   
679524   CBOH 2012-10-21    3.00        0.0   93429   
679549   CBOH 2015-02-08    3.00        0.0   93429   
679593   HSFT 2011-10-08    1.00        1.0   93431   
679599   HSFT 2012-11-18    3.00        0.0   93431   
679601   GTEC 2007-04-27    2.00        1.0   93432   
679602   GTEC 2007-09-25    3.00        0.0   93432   
679603   GTEC 2008-01-15    1.00        1.0   93432   
679604   GTEC 2008-09-29    1.00        1.0   93432   
679621   SAWN 2013-05-05    2.00        1.0   93434   
679629   TSLA 2010-08-08    3.00        0.0   93436   
679650   TSLA 2012-04-08    3.00        0.0   93436   
679682   TSLA 2014-09-01    1.00        1.0   93436   
679732   TSLA 2017-05-07    2.00        1.0   93436   

                                   cname SICCD  PRC  RET  SHROUT  sprtrn  \
209                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
235                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
241                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
271                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
295                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
311                          PLEXUS CORP   NaN  NaN  NaN     NaN     NaN   
339                          PLEXUS CORP   NaN  NaN  NaN     NaN

In [ ]:
i = 0
for indx in missing_index:
    i += 1
    print('已经完成: {}'.format(1.0*i/len(missing_crsp_sent)))
    
    permno = missing_crsp_sent['permno'][indx]
    date = missing_crsp_sent['date'][indx]
    date_str =str(pd.to_datetime(date))[:10]
    print(date)
    print(permno)
    for t in range(1, 10):       
        if df_crsp[(df_crsp['permno'] == permno) & \
                         ((df_crsp['date']) == datetime.strptime(date_str, '%Y-%m-%d') + timedelta(days=t))].index > 0:
            indx_crsp = df_crsp[(df_crsp['permno'] == permno) & \
                         ((df_crsp['date']) == datetime.strptime(date_str, '%Y-%m-%d') + timedelta(days=t))].index
            try:
                merge_sentiment_crsp['SICCD'][indx] = int(df_crsp['SICCD'][indx_crsp])
                merge_sentiment_crsp['SHROUT'][indx] = float((df_crsp['SHROUT'][indx_crsp]))
                merge_sentiment_crsp['sprtrn'][indx] = float(df_crsp['sprtrn'][indx_crsp])
                merge_sentiment_crsp['ret_shift_3'][indx] = float(df_crsp['RET'][indx_crsp - 3])
                merge_sentiment_crsp['ret_shift_2'][indx] = float(df_crsp['RET'][indx_crsp - 2])
                merge_sentiment_crsp['ret_shift_1'][indx] = float(df_crsp['RET'][indx_crsp - 1])
                merge_sentiment_crsp['RET'][indx] = float(df_crsp['RET'][indx_crsp])
                merge_sentiment_crsp['ret_1'][indx] = float(df_crsp['RET'][indx_crsp + 1])
                merge_sentiment_crsp['ret_2'][indx] = float(df_crsp['RET'][indx_crsp + 2])
                merge_sentiment_crsp['ret_3'][indx] = float(df_crsp['RET'][indx_crsp + 3])
                print(merge_sentiment_crsp[(merge_sentiment_crsp['permno'] == permno) &\
                                    (merge_sentiment_crsp['date'] == date)])
            except:
                continue
            break
 

已经完成: 3.2154340836e-05
2001-11-17 00:00:00
10032


/Users/shuhao/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:12: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if sys.path[0] == '':
/Users/shuhao/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/Users/shuhao/anaconda2/lib/python2.7/site-packages/ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/Users/shuhao/anaconda2/lib/python2.7/site-packages/ipyker

    ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
209   PLUS 2001-11-17     3.0        0.0   10032  PLEXUS CORP  3670  NaN   

       RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3     ret_1  \
209  0.035  41757.0  0.010899    0.038422     0.00662    0.014134 -0.066023   

        ret_2     ret_3  
209 -0.003103  0.020408  
已经完成: 6.4308681672e-05
2002-08-04 00:00:00
10032
    ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
235   PLUS 2002-08-04     3.0        0.0   10032  PLEXUS CORP  3670  NaN   

          RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
235 -0.085438  41945.0 -0.034296   -0.035125    0.003597   -0.061445   

        ret_1     ret_2     ret_3  
235  0.099919 -0.021418  0.015094  
已经完成: 9.6463022508e-05
2002-09-08 00:00:00
10032
    ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
241   PLUS 2002-09-08     2.5        1.0   10032  PLEXUS CORP  3670  NaN   

         RET   

     ticker       date  ireccd  sentiment  permno                 cname SICCD  \
1040   SUNW 2005-03-27     3.0        0.0   10078  SUN MICROSYSTEMS INC  3570   

      PRC RET     SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
1040  NaN   0  3406019.0  0.002441   -0.012255    0.012407   -0.042755   

         ret_1 ret_2     ret_3  
1040  0.014888     0 -0.012225  
已经完成: 0.000836012861736
2005-06-05 00:00:00
10078
     ticker       date  ireccd  sentiment  permno                 cname SICCD  \
1045   SUNW 2005-06-05     5.0        0.0   10078  SUN MICROSYSTEMS INC  3570   

      PRC       RET     SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
1045  NaN -0.010929  3406019.0  0.001246   -0.034301   -0.035623    0.031496   

         ret_1    ret_2     ret_3  
1045 -0.002762  0.00277 -0.005525  
已经完成: 0.000868167202572
2005-09-25 00:00:00
10078
     ticker       date  ireccd  sentiment  permno                 cname SICCD  \
1050   SUNW 2005-09-25     1.0        1.0   1

     ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
1665   ORCL 2008-06-01     1.0        1.0   10104  ORACLE CORP  7370  NaN   

           RET     SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
1665 -0.007005  5150000.0 -0.010504    0.002194           0    0.005737   

         ret_1 ret_2     ret_3  
1665  0.010141     0  0.011785  
已经完成: 0.00144694533762
2011-10-08 00:00:00
10104
     ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
1741   ORCL 2011-10-08     1.0        1.0   10104  ORACLE CORP  7370  NaN   

          RET     SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
1741  0.03544  5044602.0  0.034125   -0.003326    0.018977    0.028581   

         ret_1    ret_2     ret_3  
1741 -0.001292  0.00582  0.000964  
已经完成: 0.00147909967846
2012-03-11 00:00:00
10104
     ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
1750   ORCL 2012-03-11     3.0        0.0   10104  ORACLE CORP  7370  NaN   


...

       ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
490386    MRA 2002-03-17     3.0        0.0   85349  MERITOR INC  3714  NaN   

             RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
490386  0.033157  66692.0 -0.000523   -0.000705   -0.020035   -0.032096   

           ret_1     ret_2     ret_3  
490386 -0.010925  0.005868 -0.040494  
已经完成: 0.581028938907
2002-08-04 00:00:00
85349
       ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
490395    MRA 2002-08-04     2.0        1.0   85349  MERITOR INC  3714  NaN   

             RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
490395 -0.027613  67883.0 -0.034296   -0.051006    0.009924   -0.005639   

           ret_1     ret_2     ret_3  
490395  0.051724  0.030376  0.034628  
已经完成: 0.581061093248
2002-09-08 00:00:00
85349
       ticker       date  ireccd  sentiment  permno        cname SICCD  PRC  \
490397    MRA 2002-09-08     3.0        0.0   85349

       ticker       date  ireccd  sentiment  permno              cname SICCD  \
491058   NXLK 2001-11-17     3.0        0.0   85388  XO COMMUNICATIONS  4813   

        PRC       RET    SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
491058  NaN  0.192982  329963.0  0.010899    0.027027    0.037383    0.009434   

           ret_1     ret_2     ret_3  
491058 -0.036765 -0.183206  0.037383  
已经完成: 0.581672025723
2002-03-28 00:00:00
85388
已经完成: 0.581704180064
2004-01-21 00:00:00
85388
已经完成: 0.581736334405
2004-08-10 00:00:00
85388
已经完成: 0.581768488746
2005-02-10 00:00:00
85388
已经完成: 0.581800643087
2005-11-07 00:00:00
85388
已经完成: 0.581832797428
2002-08-04 00:00:00
85390
       ticker       date  ireccd  sentiment  permno                cname  \
491121   PLCE 2002-08-04     4.0        0.0   85390  CHILDRENS PLACE INC   

       SICCD  PRC       RET   SHROUT    sprtrn ret_shift_1 ret_shift_2  \
491121  5640  NaN  0.017877  26505.0 -0.034296   -0.020305    -0.03634   

       ret_shi

       ticker       date  ireccd  sentiment  permno                  cname  \
491890   AA51 2015-09-13     2.0        1.0   85418  CAMDEN NATIONAL CORP.   

       SICCD  PRC      RET  SHROUT   sprtrn ret_shift_1 ret_shift_2  \
491890  6021  NaN  0.00276  7453.0 -0.00409   -0.005242   -0.001993   

       ret_shift_3     ret_1     ret_2     ret_3  
491890   -0.009622  0.021522 -0.004165 -0.000246  
已经完成: 0.582411575563
2010-05-09 00:00:00
85419
       ticker       date  ireccd  sentiment  permno  \
491926    CSU 2010-05-09     3.0        0.0   85419   

                             cname SICCD  PRC       RET   SHROUT    sprtrn  \
491926  CAPITAL SENIOR LIVING CORP  8051  NaN  0.067347  27028.0  0.043974   

       ret_shift_1 ret_shift_2 ret_shift_3     ret_1     ret_2     ret_3  
491926   -0.006085   -0.025692    -0.05597  0.032505  0.075926 -0.096386  
已经完成: 0.582443729904
1998-09-12 00:00:00
85421
       ticker       date  ireccd  sentiment  permno             cname SICCD  \
491962 

       ticker       date  ireccd  sentiment  permno      cname SICCD  PRC  \
492281    FTE 2002-09-08     5.0        0.0   85425  ORANGE SA  4812  NaN   

             RET  SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
492281 -0.059037  1490.0  0.010113    0.094433   -0.127493    0.093928   

           ret_1     ret_2     ret_3  
492281  0.009653  0.006692 -0.017094  
已经完成: 0.583022508039
2003-05-26 00:00:00
85425
       ticker       date  ireccd  sentiment  permno      cname SICCD  PRC  \
492291    FTE 2003-05-26     1.0        1.0   85425  ORANGE SA  4812  NaN   

             RET  SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
492291  0.031329  3402.0  0.019567    0.024285    0.008749    0.009717   

           ret_1     ret_2     ret_3  
492291  0.010673  0.009342  0.007243  
已经完成: 0.583054662379
2008-06-01 00:00:00
85425
       ticker       date  ireccd  sentiment  permno      cname SICCD  PRC  \
492316    FTE 2008-06-01     3.0        0.0   85425  ORANGE SA  4

已经完成: 0.584855305466
2002-03-17 00:00:00
85440
       ticker       date  ireccd  sentiment  permno           cname SICCD  \
492753   SRI1 2002-03-17     4.0        0.0   85440  STONERIDGE INC  3714   

        PRC       RET   SHROUT    sprtrn ret_shift_1 ret_shift_2 ret_shift_3  \
492753  NaN -0.016237  22397.0 -0.000523   -0.029657   -0.009183   -0.018034   

           ret_1     ret_2     ret_3  
492753 -0.000971 -0.029155 -0.001001  
已经完成: 0.584887459807
2002-09-08 00:00:00
85442
       ticker       date  ireccd  sentiment  permno  \
492850   TSM2 2002-09-08     3.0        0.0   85442   

                                  cname SICCD  PRC       RET    SHROUT  \
492850  TAIWAN SEMICONDUCTOR MFC CO LTD  3674  NaN  0.022021  350671.0   

          sprtrn ret_shift_1 ret_shift_2 ret_shift_3     ret_1     ret_2  \
492850  0.010113    0.027963   -0.057716    0.033722  0.074778 -0.038915   

           ret_3  
492850 -0.052761  
已经完成: 0.584919614148
2003-01-12 00:00:00
85442
       ticker 

In [322]:
ibes_crsp_link[ibes_crsp_link['permno'] == 10220]

Unnamed: 0 ticker  permno                 cname                  comnam  \
2617        2737   BWCN   10220  BWX TECHNOLOGIES INC  B W X TECHNOLOGIES INC   

      name_similarity  score  
2617               95      0

In [320]:
print(df_crsp[(df_crsp['permno'] == 10220) ])
# print(merge_sentiment_crsp[(merge_sentiment_crsp['permno'] == 10064) & (merge_sentiment_crsp['date'] == '2003-03-28')])


        permno       date SICCD    PRC        RET    SHROUT    sprtrn  \
277182   10220 2010-08-02  3569  23.15          C  116226.0  0.022023   
277183   10220 2010-08-03  3569  22.37  -0.033693  116226.0 -0.004796   
277184   10220 2010-08-04  3569  23.51   0.050961  116226.0  0.006051   
277185   10220 2010-08-05  3569  24.68   0.049766  116226.0 -0.001269   
277186   10220 2010-08-06  3569  24.11  -0.023096  116226.0 -0.003704   
277187   10220 2010-08-09  3569  23.76  -0.014517  116226.0  0.005483   
277188   10220 2010-08-10  3569  23.46  -0.012626  116226.0 -0.005967   
277189   10220 2010-08-11  3569  22.95  -0.021739  116226.0 -0.028179   
277190   10220 2010-08-12  3569  22.39  -0.024401  116226.0 -0.005379   
277191   10220 2010-08-13  3569  22.03  -0.016079  116226.0 -0.004024   
277192   10220 2010-08-16  3569  22.14   0.004993  116226.0  0.000120   
277193   10220 2010-08-17  3569  22.61   0.021229  116226.0  0.012192   
277194   10220 2010-08-18  3569  23.04   0.019018  

In [218]:
startTime = datetime.now()

permnos = list(set(sentiment['permno']))
permnos.sort()
# r = np.ones((len(sentiment['date']), 10)) # create a panel with 10 columns (permno, date, sentiment, r-3, ..., r+3)
r = []
i = 0
for permno in permnos[:2]:
    dates = sentiment[sentiment['permno'] == permno]['date']
    for date in dates:
        
        print(permno)
        print(date)
        indx_ibes = sentiment[(sentiment['permno'] == permno) & (sentiment['date'] == date)].index
        senm = float(sentiment['sentiment'][indx_ibes])
        recm = float(sentiment['ireccd'][indx_ibes])
        
        if df_crsp_copy[(df_crsp_copy['permno'] == permno) & ((df_crsp_copy['date']) == date)].index > 0:
            
            indx_crsp = df_crsp_copy[(df_crsp_copy['permno'] == permno) & ((df_crsp_copy['date']) == date)].index
            r_t_s_3 = float(df_crsp_copy['RET'][indx_crsp - 3])
            r_t_s_2 = float(df_crsp_copy['RET'][indx_crsp - 2])
            r_t_s_1 = float(df_crsp_copy['RET'][indx_crsp - 1])
            r_t_0 = float(df_crsp_copy['RET'][indx_crsp])
            r_t_1 = float(df_crsp_copy['RET'][indx_crsp + 1])
            r_t_2 = float(df_crsp_copy['RET'][indx_crsp + 2])
            r_t_3 = float(df_crsp_copy['RET'][indx_crsp + 3])
        else:
            for t in range(1, 10):
                if df_crsp_copy[(df_crsp_copy['permno'] == permno) & \
                                 ((df_crsp_copy['date']) == datetime.strptime(date, '%Y-%m-%d') + timedelta(days=t))].index > 0:
                    indx_crsp = df_crsp_copy[(df_crsp_copy['permno'] == permno) & \
                                 ((df_crsp_copy['date']) == datetime.strptime(date, '%Y-%m-%d') + timedelta(days=t))].index
                    r_t_s_3 = float(df_crsp_copy['RET'][indx_crsp - 3])
                    r_t_s_2 = float(df_crsp_copy['RET'][indx_crsp - 2])
                    r_t_s_1 = float(df_crsp_copy['RET'][indx_crsp - 1])
                    r_t_0 = float(df_crsp_copy['RET'][indx_crsp])
                    r_t_1 = float(df_crsp_copy['RET'][indx_crsp + 1])
                    r_t_2 = float(df_crsp_copy['RET'][indx_crsp + 2])
                    r_t_3 = float(df_crsp_copy['RET'][indx_crsp + 3])
                    break

        r.append({'permno':permno, 'date':date, 'sentiment':senm, 'recommendation':recm,
                  'r_shit_3':r_t_s_3, 'r_shit_2':r_t_s_2, 'r_shit_1':r_t_s_1,
                  'r_0':r_t_0, 'r_0':r_t_0, 'r_1':r_t_1, 'r_2':r_t_2, 'r_3':r_t_3})
        df_crsp_copy = 
        print('已经完成： {}'.format(i/17076.))
r = pd.DataFrame(r)
print(r)
print datetime.now() - startTime 

SyntaxError: invalid syntax (<ipython-input-218-db3a4b9155d3>, line 44)

In [215]:
df_crsp_copy[10:].head()

PERMNO       date SICCD    PRC        RET  SHROUT    sprtrn ret_shift_1  \
10   10001 1992-01-16  4920  14.25  -0.050000  1075.0 -0.006084    0.034483   
11   10001 1992-01-17  4920  15.00   0.052632  1075.0  0.001554   -0.050000   
12   10001 1992-01-20  4920  14.75  -0.016667  1075.0 -0.005969    0.052632   
13   10001 1992-01-21  4920  14.25  -0.033898  1075.0 -0.008935   -0.016667   
14   10001 1992-01-22  4920  14.75   0.035088  1075.0  0.013305   -0.033898   

   ret_shift_2 ret_shift_3      ret_1      ret_2      ret_3  
10    0.000000    0.000000   0.052632  -0.016667  -0.033898  
11    0.034483    0.000000  -0.016667  -0.033898   0.035088  
12   -0.050000    0.034483  -0.033898   0.035088  -0.050847  
13    0.052632   -0.050000   0.035088  -0.050847   0.000000  
14   -0.016667    0.052632  -0.050847   0.000000   0.008929

In [242]:
df_crsp[(df_crsp['permno'] == 10011) & (df_crsp['date'] == '1995-11-21')]
# if test_index > 0:
#     print('True')
# else:
#     print('False')
# df_crsp['RET'][test_index]
# df_crsp[(df_crsp['PERMNO'] == 10032)].isna().sum()
# test
# test
# float(r['r_0'][0])


permno       date SICCD     PRC       RET  SHROUT   sprtrn ret_shift_1  \
16922   10011 1995-11-21  7390  13.375  0.028846  5857.0  0.00568   -0.009524   

      ret_shift_2 ret_shift_3      ret_1      ret_2     ret_3  
16922    0.004785    0.014563  -0.028037  -0.009615  0.019417

In [66]:

# df_crsp['date'] = pd.to_datetime(df_crsp['date'])



0       1992-01-02
1011    1996-01-02
1265    1997-01-02
1518    1998-01-02
2274    2001-01-02
2522    2002-01-02
2774    2003-01-02
3026    2004-01-02
4032    2008-01-02
4285    2009-01-02
5291    2013-01-02
5543    2014-01-02
5795    2015-01-02
1       1992-01-03
507     1994-01-03
759     1995-01-03
1012    1996-01-03
1266    1997-01-03
2022    2000-01-03
2275    2001-01-03
2523    2002-01-03
2775    2003-01-03
3278    2005-01-03
3530    2006-01-03
3781    2007-01-03
4033    2008-01-03
4789    2011-01-03
5041    2012-01-03
5292    2013-01-03
5544    2014-01-03
           ...    
8888    2001-08-29
9136    2002-08-29
9388    2003-08-29
9891    2005-08-29
10143   2006-08-29
10394   2007-08-29
10647   2008-08-29
11402   2011-08-29
11655   2012-08-29
6868    1993-08-30
7121    1994-08-30
7374    1995-08-30
7628    1996-08-30
8383    1999-08-30
8637    2000-08-30
8889    2001-08-30
9137    2002-08-30
9639    2004-08-30
9892    2005-08-30
10144   2006-08-30
10395   2007-08-30
11150   2010

In [70]:
# import datetime
# df_ibes_rec['anntims'] = df_ibes_rec['anntims'].apply(lambda x: str(datetime.timedelta(seconds=x))) 

# df_ibes_rec.sort_values(by=['ticker', 'anndats', 'anntims'], inplace=True)

# df_ibes_rec['sentiment_change'] = ''
# df_ibes_rec['recomm_change'] = ''
# df_ibes_rec['sentiment'] = ''
# df_ibes_rec.loc[df_ibes_rec['ireccd'] < 3, 'sentiment'] = 1
# df_ibes_rec.loc[df_ibes_rec['ireccd'] >= 3, 'sentiment'] = 0

# df_ibes_rec['recomm_change'] = df_ibes_rec.groupby(df_ibes_rec['ticker'])['ireccd'].apply(lambda x: x - x.shift()).fillna(0)


In [73]:
# df_ibes_rec.loc[df_ibes_rec['recomm_change'] < 0, 'sentiment_change'] = 1
# df_ibes_rec.loc[df_ibes_rec['recomm_change'] > 0 , 'sentiment_change'] = -1
# df_ibes_rec.loc[df_ibes_rec['recomm_change'] == 0, 'sentiment_change'] = 0
# df_ibes_rec.loc[df_ibes_rec['recomm_change'] == np.nan, 'sentiment_change'] = 0



# df_ibes_rec['sentiment_change'] = df_ibes_rec.loc[df_ibes_rec.groupby(df_ibes_rec['ticker'])['ireccd'].apply
#                                                   (lambda x: x - x.shift()) >= 0, 'sentiment_change'] = 0
# df_ibes_rec.head(10)

Unnamed: 0 ticker     cusip oftic           cname     anndats   anntims  \
2           2   0000  87482X10  TLMR  TALMER BANCORP  2014-03-09  17:05:00   
0           0   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   0:20:00   
1           1   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   0:25:00   
3           3   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   6:48:00   
4           4   0000  87482X10  TLMR  TALMER BANCORP  2014-03-10   7:45:00   
5           5   0000  87482X10  TLMR  TALMER BANCORP  2014-12-03   7:36:00   
6           6   0000  87482X10  TLMR  TALMER BANCORP  2015-04-30  14:03:00   
7           7   0000  87482X10  TLMR  TALMER BANCORP  2015-07-30  16:40:00   
8           8   0000  87482X10  TLMR  TALMER BANCORP  2015-08-04   8:00:00   
9           9   0000  87482X10  TLMR  TALMER BANCORP  2016-01-26  21:44:00   

   ireccd  sentiment  sentiment_change  recomm_change  
2       2          1                 0            0.0  
0       2          1                 0            0.0  
1       2          1                 0            0.0  
3       1          1                 1           -1.0  
4       3          0                -1            2.0  
5       1          1                 1           -2.0  
6       3          0                -1            2.0  
7       3          0                 0            0.0  
8       3          0                 0            0.0  
9       3          0                 0            0.0